# 5.5.3 Euler equations


state variables: 
* mass density $\rho$
* momentum $m = \rho u$, with velocity $u$
* energy density $E$

conservation of mass, momentum and energy:

\begin{eqnarray*}
\frac{\partial \rho}{\partial t} & = & -\operatorname{div} \rho u \\
\frac{\partial \rho u}{\partial t} & = & -\operatorname{div} (\rho u \otimes u + p I) \\
\frac{\partial E}{\partial t} & = & -\operatorname{div} (E+p) u
\end{eqnarray*}


closure equation for pressure: $p = (\gamma-1) (E - \rho \tfrac{1}{2} |u|^2)$ 

with heat capacity ration $\gamma$ depending on gas, $\gamma=1.4$ for atmosphere.


Compact notation:
$$
\frac{\partial U}{\partial t} + \operatorname{div} F(U) = 0
$$

with vector of state variables (in $R^{d+2}$):
$$
U = \left( \begin{array}{c}
    \rho \\ m \\ E
    \end{array} \right)
$$
and flux in $R^{(d+2) \times d}$:
$$
F = \left( \begin{array}{c}
    \rho u \\ 
    \rho u \otimes u + p I \\
    (E + p) u
    \end{array} \right)
$$



In [ ]:
from ngsolve import *
from ngsolve.webgui import Draw
from time import sleep

try:
    import ngsolve.ngscuda as ngscuda
except:
    pass

In [ ]:
mesh = Mesh(unit_square.GenerateMesh(maxh=0.02))

order=3
fesT = L2(mesh, order=order)**4
feshat = FacetFESpace(mesh, order=order)**4
fes = fesT*feshat

gfu = GridFunction(fes)
rho0 = 1+1*exp(-400*( (x-0.5)**2 + (y-0.5)**2))
with TaskManager():
    gfu.components[0].Set( (rho0, 0, 0, 1) )

In [ ]:
gamma = 1.4  # Gas constant
def Flux (U):
    rho = U[0]
    u = U[1:3]/rho
    E = U[3]
    p = (gamma-1)*(E-rho/2*(u*u))
    return CF ( (rho*u, rho*OuterProduct(u,u)+p*Id(2), 
                 (E+p)*u)).Reshape((4,2))

ngsglobals.msg_level = 0

n = specialcf.normal(2)
stab = 1
def NumFlux(u, uo): 
    return 0.5*(Flux(u)+Flux(uo)) 

In [ ]:
truecompile = False

(u,uhat), (v,vhat) = fes.TnT()
# bfa1 = BilinearForm(fes, nonassemble=True)

term1a = InnerProduct (NumFlux(u, 2*uhat-u), v.Operator("normal")).Compile(truecompile, wait=True)*dx(element_boundary=True)
term1b = (2*stab*v*(u-uhat)).Compile(truecompile, wait=True)*dx(element_vb=BND)
term2 = (-InnerProduct(Flux(u),Grad(v))).Compile(truecompile, wait=True)*dx

bfa = BilinearForm (term1a+term1b+term2, nonlinear_matrix_free_bdb=True).Assemble()

embT, embhat = fes.embeddings
resT, reshat = fes.restrictions
rangeT = fes.Range(0)
rangehat = fes.Range(1)

invm1 = embT@fesT.Mass(1).Inverse()@embT.T
# traceop = fesT.TraceOperator(feshat, average=True)
traceop = 0.5*fesT.TraceOperator(feshat, average=False)
traceop = traceop.CreateDeviceMatrix()

uT, vT = fesT.TnT()
with TaskManager():
    invm = BilinearForm(uT*vT*dx, diagonal=True).Assemble().mat.Inverse()
invm_host =  embT@invm@embT.T
invm = invm_host.CreateDeviceMatrix()

print(rangeT, rangehat)

In [ ]:
rho0 = 0.2+1*exp(-400*( (x-0.5)**2 + (y-0.5)**2))
with TaskManager():
    gfu.components[0].Set( (rho0, 0, 0, rho0) )

gfubnd = GridFunction(fes)
gfubnd.components[1].vec.data = traceop * gfu.components[0].vec
Projector(fes.GetDofs(mesh.Boundaries(".*")), True).Project(gfubnd.vec)

gf_rho = gfu.components[0][0]
gf_u = gfu.components[0][1:3] / gf_rho
gf_E = gfu.components[0][3]
gf_p = (gamma-1)*(gf_E-gf_rho/2*(gf_u*gf_u))  # pressure
gf_a = sqrt(gamma*gf_p/gf_rho)        # speed of sound
gf_M = Norm(gf_u) / gf_a              # Mach number

print ("Density")
scene_rho = Draw (gf_rho, mesh, deformation=True)
print ("Velocity")
scene_u = Draw(gf_u, mesh, vectors={"grid_size":100})
print ("Mach number")
scene_M = Draw(Norm(gf_u)/gf_a, mesh)

t = 0
tend = 0.3
tau = 1e-4 
i = 0
bfamat = bfa.mat.CreateDeviceMatrix()
traceop = traceop.CreateDeviceMatrix()
vec = gfu.vec.CreateDeviceVector()
vecbnd = gfubnd.vec.CreateDeviceVector()
hv = gfu.vec.CreateDeviceVector()
from time import time

with TaskManager():
    while t < tend:
        vec[rangehat] = traceop * vec[rangeT] + vecbnd[rangehat]
        hv.data = bfamat * vec
        vec -= tau * invm * hv
        
        t += tau
        i += 1
        if i%20 == 0:
            gfu.vec.data = vec
            scene_rho.Redraw()
            scene_u.Redraw()
            scene_M.Redraw()           

In [ ]:
print (bfamat.GetOperatorInfo())

## Code generation for the device

the volume-part of the bilinear-form

$$
\int_T F(u)  \nabla v
\qquad
\text{with}
\qquad
F = \left( \begin{array}{c}
    \rho u \\ 
    \rho u \otimes u + p I \\
    (E + p) u
    \end{array} \right)
$$

is represented in NGSolve as a list of operations:


In [ ]:
print (term2)

to extract the flux, we differentiate w.r.t. the test-function

In [ ]:
print (term2[0].coef.Diff(Grad(v)))

And for this *program* we generate low-level C-code. Only the function header and loop had to be changed for a cuda-kernel: